# Introduction
## Goal
I have a dataset I want to embed for semantic search (or QA, or RAG), I want the easiest way to do embed this and put it in a new dataset.

## Approach
Im using a dataset from my favorite subreddit [r/bestofredditorupdates](). Since it has such long entries, I will use the new [jinaai/jina-embeddings-v2-base-en](https://huggingface.co/jinaai/jina-embeddings-v2-base-en) since it has an 8k context length. Since Im GPU-poor I will deploy this using [Inference Endpoint](https://huggingface.co/inference-endpoints) to save money and time. To follow this you will need to add a payment method. To make it even easier, I'll make this fully API based.

# Setup

## Imports

In [1]:
import asyncio
from getpass import getpass
import json
from pathlib import Path
import time

from aiohttp import ClientSession, ClientTimeout
from datasets import load_dataset, Dataset, DatasetDict
from huggingface_hub import notebook_login
import pandas as pd
import requests
from tqdm.auto import tqdm

## Config
You need to fill this in with your desired repos. Note I used 5 for the `MAX_WORKERS` since `jina-embeddings-v2` are quite memory hungry. 

In [2]:
dataset_in = 'derek-thomas/dataset-creator-reddit-bestofredditorupdates'
dataset_out = "processed-bestofredditorupdates"
endpoint_name = "boru-jina-embeddings-demo"

MAX_WORKERS = 5  

In [3]:
username = getpass(prompt="What is your Hugging Face 🤗 username? (with an added payment method)")
hf_token = getpass(prompt='What is your Hugging Face 🤗 token?')

What is your Hugging Face 🤗 username? (with a credit card) ········
What is your Hugging Face 🤗 token? ········


## Get Dataset

In [4]:
dataset = load_dataset(dataset_in, token=hf_token)
dataset['train']

Dataset({
    features: ['date_utc', 'title', 'flair', 'content', 'poster', 'permalink', 'id', 'content_length', 'score'],
    num_rows: 9991
})

In [5]:
documents = dataset['train'].to_pandas().to_dict('records')
len(documents), documents[0]

(9991,
 {'date_utc': Timestamp('2022-12-31 18:16:22'),
  'title': 'To All BORU contributors, Thank you :)',
  'flair': 'CONCLUDED',
  'content': '[removed]',
  'poster': 'IsItAcOnSeQuEnCe',
  'permalink': '/r/BestofRedditorUpdates/comments/10004zw/to_all_boru_contributors_thank_you/',
  'id': '10004zw',
  'content_length': 9,
  'score': 1})

# Inference Endpoints
## Create Inference Endpoint
We are going to use the [API](https://huggingface.co/docs/inference-endpoints/api_reference) to create an [Inference Endpoint](https://huggingface.co/inference-endpoints). This should provide a few main benefits:
- It's convenient (No clicking)
- It's repeatable (We have the code to run it easily)
- It's cheaper (No time spent waiting for it to load, and automatically shut it down)

In [6]:
headers = {
	"Authorization": f"Bearer {hf_token}",
	"Content-Type": "application/json"
}
base_url = f"https://api.endpoints.huggingface.cloud/v2/endpoint/{username}"
endpoint_url = f"https://api.endpoints.huggingface.cloud/v2/endpoint/{username}/{endpoint_name}"

There are a few design choices here:
- I'm using the `g5.2xlarge` since it is big and `jina-embeddings-v2` are memory hungry (remember the 8k context length). 
- I didnt alter the default `MAX_BATCH_TOKENS` or `MAX_CONCURRENT_REQUESTS`
    - You should consider this if you are making this production ready
    - You will need to restrict these to match the HW you are running on
- As mentioned before, I chose the repo and the corresponding revision


In [7]:
data = {
    "accountId": None,
    "compute": {
        "accelerator": "gpu",
        "instanceType": "g5.2xlarge",
        "instanceSize": "medium",
        "scaling": {
            "maxReplica": 1,
            "minReplica": 1
        }
    },
    "model": {
        "framework": "pytorch",
        "image": {
          "custom": {
            "url": "ghcr.io/huggingface/text-embeddings-inference:0.3.0",
            "health_route": "/health",
            "env": {
              "MAX_BATCH_TOKENS": "16384",
              "MAX_CONCURRENT_REQUESTS": "512",
              "MODEL_ID": "/repository"
            }
          }
        },
        "repository": "jinaai/jina-embeddings-v2-base-en",
        "revision": "8705ed9657208b2d5220fffad1c3a30980d279d0",
        "task": "sentence-embeddings",
    },
    "name": endpoint_name,
    "provider": {
        "region": "us-east-1",
        "vendor": "aws"
    },
    "type": "protected"
}

response = requests.post(base_url, headers={**headers, 'accept': 'application/json'}, json=data)


print(response.status_code)

202


## Wait until its running
Here we use `tqdm` as a pretty way of displaying our status. It took about ~30s for this model to get the Inference Endpoint running.

In [8]:
with tqdm(desc="Waiting for status to change", unit="s") as pbar:
    while True:
        response_json = requests.get(endpoint_url, headers=headers).json()
        current_status = response_json['status']['state']

        if current_status == 'running':
            print("Status is 'running'.")
            break

        pbar.set_description(f"Status: {current_status}")
        time.sleep(2)
        pbar.update(1)

embedding_url = response_json['status']['url']

Waiting for status to change: 0s [00:00, ?s/s]

Status is 'running'.


I found that even though the status is running, I want to get a test message to run first before running our batch in parallel.

In [9]:
payload = {"inputs": "This sound track was beautiful! It paints the senery in your mind so well I would recomend it even to people who hate vid. game music!"}

with tqdm(desc="Waiting for endpoint to accept requests", unit="s") as pbar:
    while True:
        try:
            response_json = requests.post(embedding_url, headers=headers, json=payload).json()

            # Assuming the successful response has a specific structure
            if len(response_json[0]) == 768:
                print("Endpoint is accepting requests")
                break

        except requests.ConnectionError as e:
            pass

        # Delay between retries
        time.sleep(5)
        pbar.update(1)


Waiting for endpoint to accept requests: 0s [00:00, ?s/s]

Endpoint is accepting requests


# Get Embeddings

Here I send a document, update it with the embedding, and return it. This happens in parallel with `MAX_WORKERS`.

In [10]:
async def request(document, semaphore):
    # Semaphore guard
    async with semaphore:
        payload = {
            "inputs": document['content'] or document['title'] or '[deleted]',
            "truncate": True
        }
        
        timeout = ClientTimeout(total=10)  # Set a timeout for requests (10 seconds here)

        async with ClientSession(timeout=timeout, headers=headers) as session:
            async with session.post(embedding_url, json=payload) as resp:
                if resp.status != 200:
                    raise RuntimeError(await resp.text())
                result = await resp.json()
                
        document['embedding'] = result[0]  # Assuming the API's output can be directly assigned
        return document

async def main(documents):
    # Semaphore to limit concurrent requests. Adjust the number as needed.
    semaphore = asyncio.BoundedSemaphore(MAX_WORKERS)

    # Creating a list of tasks
    tasks = [request(document, semaphore) for document in documents]
    
    # Using tqdm to show progress. It's been integrated into the async loop.
    for f in tqdm(asyncio.as_completed(tasks), total=len(documents)):
        await f

In [11]:
start = time.perf_counter()

# Get embeddings
await main(documents)

# Make sure we got it all
count = 0
for document in documents:
    if document['embedding'] and len(document['embedding']) == 768:
        count += 1
print(f'Embeddings = {count} documents = {len(documents)}')

            
# Print elapsed time
elapsed_time = time.perf_counter() - start
minutes, seconds = divmod(elapsed_time, 60)
print(f"{int(minutes)} min {seconds:.2f} sec")

  0%|          | 0/9991 [00:00<?, ?it/s]

Embeddings = 9991 documents = 9991
32 min 14.53 sec


## Pause Inference Endpoint
Now that we have finished, lets pause the endpoint so we don't incur any extra charges, this will also allow us to analyze the cost.

In [12]:
response = requests.post(endpoint_url + '/pause', headers=headers)

print(response.status_code)
print(response.json()['status']['state'])

200
paused


# Push updated dataset to Hub
We now have our documents updated with the embeddings we wanted. First we need to convert it back to a `Dataset` format. I find its easiest to go from list of dicts -> `pd.DataFrame` -> `Dataset`

In [13]:
df = pd.DataFrame(documents)
dd = DatasetDict({'train': Dataset.from_pandas(df)})

In [14]:
dd.push_to_hub(dataset_out, token=hf_token)

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

# Analyze Usage
1. Go to your `dashboard_url` printed below
1. Click on the Usage & Cost tab
1. See how much you have spent

In [15]:
dashboard_url = f'https://ui.endpoints.huggingface.co/{username}/endpoints/{endpoint_name}'
print(dashboard_url)

https://ui.endpoints.huggingface.co/HF-test-lab/endpoints/boru-jina-embeddings-demo


In [16]:
input("Hit enter to continue with the notebook")

Hit enter to continue with the notebook 


''

We can see that it only took `$0.71` to pay for this!

![Cost](https://huggingface.co/spaces/derek-thomas/processing-bestofredditorupdates/resolve/main/media/automatic-embeddings-cost.png)

# Delete Endpoint
We should see a `200` if everything went correctly.

In [17]:
response = requests.delete(endpoint_url, headers=headers)

print(response.status_code)

200
